In [1]:
import gym
import numpy as np
import pandas as pd
from collections import deque
import random
import gym_ple

couldn't import doomish
Couldn't import doom


In [2]:
env = gym.make('CartPole-v1')
print(env.action_space.n)
print(env.observation_space)

[2018-01-29 22:21:44,963] Making new env: CartPole-v1


2
Box(4,)


In [ ]:
from keras.models import Sequential
from keras.layers import Dense
from keras.optimizers import Adam

# Deep Q-learning Agent
class DQNAgent:
    def __init__(self, state_size, action_size):
        self.state_size = state_size
        self.action_size = action_size
        self.memory = deque(maxlen=4096)
        
        self.state_model = self._build_state_model()
        self.reward_model = self._build_reward_model()
    
    def _build_state_model(self):
        model = Sequential()
        model.add(Dense(16, input_dim=self.state_size + self.action_size, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(self.state_size))
        model.compile(loss='mse', optimizer='adam')
        return model

    def _build_reward_model(self):
        model = Sequential()
        model.add(Dense(16, input_dim=self.state_size, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(16, activation='selu'))
        model.add(Dense(1, activation='linear'))
        model.compile(loss='mse', optimizer='adam')
        return model
    
    def feedback(self, state, action, next_state, reward, done):
        a = [1.0, 0.0] if action == 0 else [0.0, 1.0]
        inp = np.asarray([a+[state[i] for i in range(self.state_size)]])
        reward_mask = 0 if done else 1
        
        target_reward = reward + reward_mask * self.reward_model.predict(next_state.reshape(1, self.state_size))[0]
        
        self.state_model.fit(inp, next_state.reshape(1,self.state_size))
        self.reward_model.fit(state.reshape(1,self.state_size), [target_reward])
    
    def remember(self, state, action, next_state, reward, done):
        self.memory.append((state, action, next_state, reward, done))
        
    def act(self, state):
        # 1. predict next state for each action
        s = np.asarray([
            [1.0, 0.0] + [state[i] for i in range(self.state_size)],
            [0.0, 1.0] + [state[i] for i in range(self.state_size)]
        ])
        pred_state = self.state_model.predict(s)
        
        #if self.bored > .5:
        #    return np.amin(self.reward_model.predict(pred_state))
        #else:
        action = np.argmax(self.reward_model.predict(pred_state)[:,0])
        return action
    
    def replay(self):
        state = np.asarray([m[0] for m in self.memory])
        action = [m[1] for m in self.memory]
        next_state = np.asarray([m[2] for m in self.memory])
        reward = [m[3] for m in self.memory]
        done = np.asarray([m[4] for m in self.memory])
        
        next_state_max_q = np.max(self.model.predict(next_state), axis=1)
        q_a = reward + (1 - done) * self.gamma * next_state_max_q
        
        pred_q = self.model.predict(state)
        target_q = np.asarray([[q_a[index], pred[1]] if action == 0 else [pred[0], q_a[index]] for index, (pred, action) in enumerate(zip(pred_q, action))])
        
        self.model.fit(
            state, 
            target_q, 
            epochs=3, 
            shuffle=True, 
            validation_split=0,
            verbose=0, 
            batch_size=16
        )
        
        self.epsilon *= self.epsilon_decay

In [ ]:
REPLAY_INTERVAL = 1

episodes = 200000
agent = DQNAgent(env.observation_space.shape[0], env.action_space.n)

for e in range(episodes):
    state = env.reset()

    for time_t in range(500):
        env.render()
        
        action = agent.act(state)
        next_state, reward, done, _ = env.step(action)
                
        agent.feedback(state, action, next_state, reward, done)
        
        state = next_state
        
        if done:
            # print the score and break out of the loop
            print("episode: {}/{}, score: {}"
                  .format(e, episodes, time_t))
            break


    #if (e+1) % REPLAY_INTERVAL == 0:
    #    agent.replay()


Epoch 1/1
1/1 [==============================] - 1s 996ms/step - loss: 0.2230
Epoch 1/1
1/1 [==============================] - 1s 1s/step - loss: 0.1156
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.1269
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0967
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.3478
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.2664
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.9959
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.4160
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 1.7475
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.5439
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 2.3586
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.6401
Epoch 1/1
1/1 [==============================] - 0s 9ms/step - loss: 2.9323
Epoch 1/1
1

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 11.1965
episode: 3/200000, score: 13
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.1648
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.5358
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0951
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0083
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0305
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.1061
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0100
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.1651
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0065
Epoch 1/1
1/1 [==============================] - 0s 7ms/step - loss: 0.2431
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.0093
Epoch 1/1
1/1 [==============================] - 0s 3ms/st

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.7836
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0040
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 1.2216
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0022
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 1.0102
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0090
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.9477
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0055
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.9969
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0107
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.9456
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0128
Epoch 1/1
1/1 [==============================] - 0s 6ms/step - loss: 46.6813
episode: 8/

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.7674
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0068
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 1.1641
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0063
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.7427
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 1.1471
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0077
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.7209
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 1/1
1/1 [==============================] - 0s 6ms/step - loss: 1.1223
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.0131
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 68.1899
episode: 13

Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 1.0725
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0061
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 82.2093
episode: 17/200000, score: 13
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0027
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 1.8732
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0028
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 1.1723
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0056
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.9861
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0031
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.7637
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0044
Epoch 1/1
1/1 [==============================] - 0s 4ms/s

...

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0053
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 6.8890
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 8.2731e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.4218
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0056
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 7.2939
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0011
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.5071
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0055
Epoch 1/1
1/1 [==============================] - 0s 6ms/step - loss: 7.8471
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0011
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.6267
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0050
Epoch 1/

Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0991
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0016
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 2.7188
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0017
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0890
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0012
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 2.5771
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0012
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.1082
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 8.4149e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 2.2712
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 8.0930e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.1641
Epoc

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0877
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0024
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 2.0301
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0037
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 2.3742
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 9.8822e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.8052
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0023
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 1.4429
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 4.5355e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.2110
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0014
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 1.0394
Epoc

Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0031
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 2.0305
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0014
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 13.2532
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0023
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 8.2320
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 8.3326e-04
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 22.8566
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0022
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 25.5270
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 6.7657e-04
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 44.4480
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0045


Epoch 1/1
1/1 [==============================] - 0s 6ms/step - loss: 2.8262
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0049
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 0.1344
Epoch 1/1
1/1 [==============================] - 0s 2ms/step - loss: 0.0099
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 5.1737
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0037
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.9890
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 0.0043
Epoch 1/1
1/1 [==============================] - 0s 6ms/step - loss: 6.7842
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0056
Epoch 1/1
1/1 [==============================] - 0s 5ms/step - loss: 2.3962
Epoch 1/1
1/1 [==============================] - 0s 4ms/step - loss: 0.0037
Epoch 1/1
1/1 [==============================] - 0s 3ms/step - loss: 8.9747
Epoch 1/1
1/